In [1]:
import time

import numpy as np
import pandas as pd
from sklearn.discriminant_analysis import (
    LinearDiscriminantAnalysis,
    QuadraticDiscriminantAnalysis,
)
from sklearn.ensemble import GradientBoostingClassifier, RandomForestClassifier
from sklearn.feature_selection import (
    RFE,
    SelectFromModel,
    SelectKBest,
    SequentialFeatureSelector,
    f_classif,
    mutual_info_classif,
)
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from utils import (
    experiment,
    get_data,
    get_param_combinations,
    get_params_json,
    save_results,
)

from xgboost import XGBClassifier

c:\Users\Tomcio\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\utils\__init__.py:16: UserWarning: A NumPy version >=1.22.4 and <2.3.0 is required for this version of SciPy (detected version 1.21.0)
  from scipy.sparse import issparse


In [2]:
X, y = get_data()

In [3]:
def run_experiment(feature_selectors, classifiers, ks, results, train_test_seeds=[42]):
    for fs in feature_selectors:
        for clf in classifiers:
            for k in ks:
                # Generate parameter combinations
                fs_cls, fs_params, k_param_name, requires_estimator = fs
                clf_cls, clf_params = clf

                fs_param_combinations = get_param_combinations(fs_params)
                clf_param_combinations = get_param_combinations(clf_params)

                for fs_params in fs_param_combinations:
                    for clf_params in clf_param_combinations:
                        result = experiment(
                            X,
                            y,
                            fs_cls,
                            fs_params,
                            clf_cls,
                            clf_params,
                            k,
                            k_param_name,
                            requires_estimator,
                            train_test_seeds,
                        )

                        print(result)
                        print(f"Elapsed time: {result[-1]:.2f}s\n")
                        results.append(result)
                        save_results(results, filename)

In [4]:
results = []

filename = "tomkowe_tree"

feature_selectors = [
    (SelectFromModel, {"threshold": [-np.inf]}, "max_features", True)
]

classifiers = [
    (
        XGBClassifier,
        {
            "booster": ["gbtree"],
            "device": ["gpu"],
            "learning_rate": [0.001, 0.01, 0.1, 0.3, 0.5],
            "n_estimators": [10, 75, 150],
            "min_child_weight": [0.5, 1, 3, 5],
            "max_depth": [2, 6, 10],
            "tree_method": ["auto", "hist", "approx"]
        },
    )
]

ks = np.arange(1, 10, 1)
train_test_seeds = list(range(42, 45))

run_experiment(feature_selectors, classifiers, ks, results, train_test_seeds)

c:\Users\Tomcio\AppData\Local\Programs\Python\Python39\lib\site-packages\xgboost\core.py:160: UserWarning: [01:08:21] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-0b3782d1791676daf-1\xgboost\xgboost-ci-windows\src\common\error_msg.cc:58: Falling back to prediction using DMatrix due to mismatched devices. This might lead to higher memory usage and slower performance. XGBoost is running on: cuda:0, while the input data is on: cpu.
Potential solutions:
- Use a data structure that matches the device ordinal in the booster.
- Set the device for booster before call to inplace_predict.

This warning will only be shown once.

  warnings.warn(smsg, UserWarning)


42 0.546
43 0.547
44 0.558
('SelectFromModel', "{'threshold': -Infinity}", 'XGBClassifier', "{'booster': 'gbtree', 'device': 'gpu', 'learning_rate': 0.001, 'n_estimators': 10, 'min_child_weight': 0.5, 'max_depth': 2, 'tree_method': 'auto'}", 1, 0.5503333333333333, 0.005436502143433369, 0.6116666666666667, 0.4591035842895508)
Elapsed time: 0.46s

42 0.546
43 0.547
44 0.558
('SelectFromModel', "{'threshold': -Infinity}", 'XGBClassifier', "{'booster': 'gbtree', 'device': 'gpu', 'learning_rate': 0.001, 'n_estimators': 10, 'min_child_weight': 0.5, 'max_depth': 2, 'tree_method': 'hist'}", 1, 0.5503333333333333, 0.005436502143433369, 0.6116666666666667, 0.2832772731781006)
Elapsed time: 0.28s

42 0.546
43 0.547
44 0.558
('SelectFromModel', "{'threshold': -Infinity}", 'XGBClassifier', "{'booster': 'gbtree', 'device': 'gpu', 'learning_rate': 0.001, 'n_estimators': 10, 'min_child_weight': 0.5, 'max_depth': 2, 'tree_method': 'approx'}", 1, 0.5503333333333333, 0.005436502143433369, 0.6116666666666

KeyboardInterrupt: 

In [4]:
results = []

filename = "tomkowe_linear"

feature_selectors = [
    (SelectFromModel, {"threshold": [-np.inf]}, "max_features", True)
]

classifiers = [
    (
        XGBClassifier,
        {
            "booster": ["gblinear"],
            "device": ["gpu"],
            "learning_rate": [0.001, 0.01, 0.1, 0.2, 0.3, 0.5],
            "n_estimators": [10, 100, 200, 300],
            "updater": ["coord_descent", "shotgun"]
        }
    )
]

ks = np.arange(1, 10, 1)
train_test_seeds = list(range(42, 47))

run_experiment(feature_selectors, classifiers, ks, results, train_test_seeds)

42 0.501
43 0.501
44 0.502
45 0.501
46 0.501
('SelectFromModel', "{'threshold': -Infinity}", 'XGBClassifier', "{'booster': 'gblinear', 'device': 'gpu', 'learning_rate': 0.001, 'n_estimators': 10, 'updater': 'coord_descent'}", 1, 0.5012, 0.00040000000000000034, 0.505, 1.261199426651001)
Elapsed time: 1.26s

42 0.501
43 0.501
44 0.502
45 0.501
46 0.501
('SelectFromModel', "{'threshold': -Infinity}", 'XGBClassifier', "{'booster': 'gblinear', 'device': 'gpu', 'learning_rate': 0.001, 'n_estimators': 10, 'updater': 'shotgun'}", 1, 0.5012, 0.00040000000000000034, 0.505, 0.17819948196411134)
Elapsed time: 0.18s

42 0.505
43 0.509
44 0.496
45 0.495
46 0.503
('SelectFromModel', "{'threshold': -Infinity}", 'XGBClassifier', "{'booster': 'gblinear', 'device': 'gpu', 'learning_rate': 0.001, 'n_estimators': 100, 'updater': 'coord_descent'}", 1, 0.5016, 0.005351635264103866, 0.506, 11.837090826034546)
Elapsed time: 11.84s

42 0.505
43 0.509
44 0.496
45 0.495
46 0.503
('SelectFromModel', "{'threshold':

KeyboardInterrupt: 

In [4]:
from sklearn.neural_network import MLPClassifier

In [5]:
results = []

filename = "tomkowe_MLP"

feature_selectors = [
    (SelectFromModel, {"threshold": [-np.inf]}, "max_features", True)
]

classifiers = [
    (
        MLPClassifier,
        {
            "hidden_layer_sizes": [(100,), (50, 50), (25, 25, 25), (10, 10, 10, 10), (15, 50, 15)],
            "activation": ["identity", "logistic", "tanh", "relu"],
            "solver": ["lbfgs", "adam", "sgd"],
            "alpha": [0.0001, 0.001, 0.01],
            "learning_rate_init": [0.001, 0.01, 0.1],
            "max_iter": [500]
        },
    )
]

ks = np.arange(1, 11, 1)
train_test_seeds = list(range(42, 45))

run_experiment(feature_selectors, classifiers, ks, results, train_test_seeds)

42 0.494
43 0.518
44 0.533
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [100], 'activation': 'identity', 'solver': 'lbfgs', 'alpha': 0.0001, 'learning_rate_init': 0.001, 'max_iter': 500}", 1, 0.515, 0.016062378404209026, 0.6083333333333333, 0.06086119016011556)
Elapsed time: 0.06s

42 0.495
43 0.517
44 0.533
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [100], 'activation': 'identity', 'solver': 'lbfgs', 'alpha': 0.0001, 'learning_rate_init': 0.01, 'max_iter': 500}", 1, 0.515, 0.015577761927397243, 0.6083333333333333, 0.05597766240437826)
Elapsed time: 0.06s

42 0.495
43 0.518
44 0.534
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [100], 'activation': 'identity', 'solver': 'lbfgs', 'alpha': 0.0001, 'learning_rate_init': 0.1, 'max_iter': 500}", 1, 0.5156666666666666, 0.016006942938057305, 0.6083333333333333, 0.05799992879231771)
Elapsed time: 0.06s

42 0.495


c:\Users\Tomcio\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:546: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


42 0.545


c:\Users\Tomcio\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:546: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


43 0.565


...

44 0.589
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'adam', 'alpha': 0.001, 'learning_rate_init': 0.01, 'max_iter': 500}", 9, 0.5913333333333334, 0.0135728487143349, 0.71, 36.327805042266846)
Elapsed time: 36.33s

42 0.617
43 0.642
44 0.608
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'adam', 'alpha': 0.001, 'learning_rate_init': 0.1, 'max_iter': 500}", 9, 0.6223333333333333, 0.014383632673594292, 0.6883333333333334, 9.336495717366537)
Elapsed time: 9.34s

42 0.522
43 0.531
44 0.519
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'adam', 'alpha': 0.01, 'learning_rate_init': 0.001, 'max_iter': 500}", 9, 0.524, 0.00509901951359279, 0.5583333333333332, 2.3928584257761636)
Elapsed time: 2.39s



c:\Users\Tomcio\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (500) reached and the optimization hasn't converged yet.
  warnings.warn(


42 0.64
43 0.669
44 0.687
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'adam', 'alpha': 0.01, 'learning_rate_init': 0.01, 'max_iter': 500}", 9, 0.6653333333333334, 0.019362047641943495, 0.73, 27.30327836672465)
Elapsed time: 27.30s

42 0.664
43 0.682
44 0.69
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'adam', 'alpha': 0.01, 'learning_rate_init': 0.1, 'max_iter': 500}", 9, 0.6786666666666666, 0.0108730042868667, 0.7466666666666667, 6.425113360087077)
Elapsed time: 6.43s

42 0.512
43 0.524
44 0.509
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'sgd', 'alpha': 0.0001, 'learning_rate_init': 0.001, 'max_iter': 500}", 9, 0.515, 0.006480740698407866, 0.59, 1.2966797351837158)
Elapsed time: 1.30s

42 0.501
43 0.499


c:\Users\Tomcio\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:698: UserWarning: Training interrupted by user.
  warnings.warn("Training interrupted by user.")


44 0.501
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'sgd', 'alpha': 0.0001, 'learning_rate_init': 0.01, 'max_iter': 500}", 9, 0.5003333333333333, 0.0009428090415820641, 0.5, 1.0501747926076253)
Elapsed time: 1.05s

42 0.501
43 0.501
44 0.501
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'sgd', 'alpha': 0.0001, 'learning_rate_init': 0.1, 'max_iter': 500}", 9, 0.501, 0.0, 0.44, 1.8316478729248047)
Elapsed time: 1.83s

42 0.514
43 0.486
44 0.525
('SelectFromModel', "{'threshold': -Infinity}", 'MLPClassifier', "{'hidden_layer_sizes': [50, 50], 'activation': 'logistic', 'solver': 'sgd', 'alpha': 0.001, 'learning_rate_init': 0.001, 'max_iter': 500}", 9, 0.5083333333333333, 0.01641814714136635, 0.5866666666666667, 1.1806008021036785)
Elapsed time: 1.18s

42 0.506
43 0.513
44 0.501
('SelectFromModel', "{'threshold':

In [23]:
pd.set_option('display.max_rows', None)

In [24]:
col_ranking = pd.read_csv("../results/rfe_rf.csv")

col_ranking.sort_values("Ranking")

cols=[105,100,101,102,103,104,8,113,2,391]

Ranking  Support
105        1     True
100        2    False
101        3    False
102        4    False
103        5    False
104        6    False
8          7    False
113        8    False
2          9    False
391       10    False
0         11    False
281       12    False
241       13    False
109       14    False
287       15    False
9         16    False
324       17    False
214       18    False
295       19    False
351       20    False
373       21    False
213       22    False
321       23    False
3         24    False
139       25    False
177       26    False
316       27    False
5         28    False
133       29    False
78        30    False
21        31    False
108       32    False
360       33    False
464       34    False
182       35    False
323       36    False
161       37    False
4         38    False
53        39    False
57        40    False
175       41    False
270       42    False
6         43    False
439       44    False
157       45    False
36        46    False
246       47    False
20        48    False
357       49    False
447       50    False
460       51    False
50        52    False
131       53    False
329       54    False
176       55    False
319       56    False
283       57    False
420       58    False
208       59    False
1         60    False
422       61    False
359       62    False
120       63    False
264       64    False
462       65    False
123       66    False
45        67    False
67        68    False
265       69    False
215       70    False
158       71    False
403       72    False
216       73    False
302       74    False
7         75    False
44        76    False
243       77    False
202       78    False
234       79    False
489       80    False
190       81    False
256       82    False
122       83    False
314       84    False
458       85    False
381       86    False
199       87    False
248       88    False
498       89    False
60        90    False
451       91    False
112       92    False
39        93    False
220       94    False
486       95    False
152       96    False
300       97    False
155       98    False
117       99    False
126      100    False
87       101    False
217      102    False
106      103    False
494      104    False
90       105    False
253      106    False
129      107    False
198      108    False
388      109    False
252      110    False
41       111    False
372      112    False
328      113    False
327      114    False
409      115    False
191      116    False
145      117    False
395      118    False
74       119    False
35       120    False
251      121    False
235      122    False
268      123    False
73       124    False
470      125    False
412      126    False
418      127    False
396      128    False
80       129    False
392      130    False
225      131    False
97       132    False
309      133    False
293      134    False
153      135    False
59       136    False
228      137    False
206      138    False
84       139    False
148      140    False
496      141    False
28       142    False
230      143    False
29       144    False
311      145    False
27       146    False
325      147    False
407      148    False
463      149    False
75       150    False
138      151    False
419      152    False
411      153    False
255      154    False
430      155    False
83       156    False
211      157    False
13       158    False
459      159    False
339      160    False
34       161    False
445      162    False
405      163    False
170      164    False
452      165    False
247      166    False
404      167    False
310      168    False
70       169    False
335      170    False
156      171    False
193      172    False
332      173    False
446      174    False
442      175    False
487      176    False
455      177    False
142      178    False
205      179    False
98       180    False
146      181    False
1